In [1]:
import numpy as np
import pandas as pd
import os
from scipy.fftpack import dct



import unicodedata
import string
import re
import random
import time
import math


from utils import token_regularizer
from utils import pair_files
from utils import load_encode
from torch.utils.data import Dataset, DataLoader, random_split

from collections import defaultdict

import json
import random

from dataset import Seq2SeqDataset, seq2seq_collate_fn


import torch
import torch.nn as nn
from torch.autograd import Variable
from torch import optim
import torch.nn.functional as F

*The path of the data

In [2]:
the_path = '/afs/inf.ed.ac.uk/group/cstr/projects/galatea/d02'
data_path_motion = the_path + '/Recordings_October_2014/DOF-hiroshi/'
data_path_text = the_path + '/Recordings_October_2014/Transcriptions/transcriptions_phrase_tables/'

paired_file_paths = pair_files(data_path_text, '.TABLE', data_path_motion,'.qtn')

In [3]:
    def is_number(s: str) -> bool:
        try:
            float(s)
            return True
        except ValueError:
            return False

In [4]:
total_words = defaultdict(dict)
for i in range(len(paired_file_paths)):
    with open(paired_file_paths[i][1],'r') as f:
        for line in f.readlines():
            line = line.strip().split()
            for j in range(3,len(line)):
                words = token_regularizer(line[j])
                for w in words:
                    if(w not in total_words):
                        total_words[w] = 1
                    else:
                        total_words[w] += 1
                
                
# print(total_words)

##所有文件中的词个数

In [5]:
vocab_to_int = {}
value = 0

for word in total_words.keys():
    if '-' not in word:
        vocab_to_int[word] = value
        value += 1
codes = ["<UNK>","<PAD>","<EOS>","<GO>","<Stammer>","<Long>"]

for code in codes:
    vocab_to_int[code] = len(vocab_to_int)

int_to_vocab = {}
for word,value in vocab_to_int.items():
    int_to_vocab[value] = word


In [23]:
a = ['Soph_02_e_Soph,2.21,2.6,COOL,221,260']
a[0].split(',')

['Soph_02_e_Soph', '2.21', '2.6', 'COOL', '221', '260']

In [6]:
def convert_to_ints(text):
    ints = []
    ints.append(vocab_to_int["<GO>"])
    for sentense in text:
        sentense_ints = 0
        for word in sentense.split():
            if word in vocab_to_int:
                sentense_ints = vocab_to_int[word]
            elif word[len(word)-1] == '-':
                sentense_ints = vocab_to_int["<Stammer>"]
            elif '-' in word:
                sentense_ints = vocab_to_int["<Long>"]
            else:
                sentense_ints = vocab_to_int["<UNK>"]
#         if eos:
#             sentense_ints.append(vocab_to_int["<EOS>"])
        ints.append(sentense_ints)
    ints.append(vocab_to_int["<EOS>"])
    return ints
    

In [16]:
def seq2seq_preprocess(transcript_path: str, motion_path: str, 
                       dictionary: dict) -> (np.ndarray, np.ndarray):
    transcripts = []
    intervals = []

    prev_sentense = ''
    prev_interval = [0,0]
    with open(transcript_path, 'r') as f:
        for line in f.readlines():
            line = line.strip().split()
            if not is_number(line[1]) or not is_number(line[2]):
                continue
            start_time = int(float(line[1]) * 100)
            end_time = int(float(line[2])*100)
            text = line[3:]
            
#             if len(text) < 5:
#                 continue 
#                 去掉过短句子
            
            if(float(line[1]) - prev_interval[1]/100.0 <= 0.5):
                prev_sentense += text
                prev_interval[1] = end_time
            else:
                transcripts.append(convert_to_ints(prev_sentense))
                intervals.append(prev_interval)
                prev_sentense = text
                prev_interval = [start_time,end_time]

                
                

    motions = np.loadtxt(motion_path, usecols=range(4), skiprows=17, 
                         dtype='float')
    
    num_dof = 4
    targets = []
    for period in intervals[1:]:
        start_time = period[0]
        end_time = period[1]

        temp_motion = motions[start_time:end_time]
        temp_motion = np.array(temp_motion)

        targets.append(temp_motion)
        
    inputs =  np.array(transcripts[1:])
    print(inputs)
    print(targets)
#     print(len(inputs))
#     print(len(targets))
    return inputs, targets

# make_dataset(seq2seq_preprocess, paired_file_paths, 'n',
#                 './data/extro_seq2seq_dataset')
# print('extroverted data finished')

In [8]:
word2idx = vocab_to_int

In [17]:
def make_dataset(process_function, paired_file_paths: list, ptype: str,
                 save_path: str) -> None:
    """"Calls preprocess methods and save processed data.

    Args:
        process_function: the function for proprecessing, it can be
            'dct_preprocess' or 'seq2seq_preprocess'.
        paired_file_paths: the output from 'pair_files' function. Its format is
            [NAME_NUM_[ine], actual text path, actual motion path]
        ptype: type of personality, can be '(e)xtroverted', '(i)ntroverted' and
            '(n)atural'.
        save_path: path to save the dataset
    """
    assert ptype in {
        'e', 'i', 'n'
    }, ('personality type should be "e","i" or "n", not %r' % ptype)

    all_input = []
    all_target = []

    input_train = []
    input_valid = []
    input_test = []

    target_train = []
    target_valid = []
    target_test = []
    # apply 'preprocess' method to for each text/motion pair
    for pair in paired_file_paths:
        # the last letter of file name means speaker's personality

        if pair[0][-1] == ptype:
            inputs, targets = process_function(pair[1], pair[2], word2idx)
            all_input.append(inputs)
            all_target.append(targets)

    train_size = int(0.8 * len(all_input))
    valid_size = int(0.1 * len(all_input))
    test_size = len(all_input) - train_size - valid_size

    for i in range(0, train_size):
        for j in range(0, len(all_input[i])):
            input_train.append(all_input[i][j])


    for i in range(train_size, train_size + valid_size):
        for j in range(0, len(all_input[i])):
            input_valid.append(all_input[i][j])

    for i in range(train_size+valid_size, len(all_input)):
        for j in range(0, len(all_input[i])):
            input_test.append(all_input[i][j])



    for i in range(0, train_size):
        for j in range(0, len(all_target[i])):
            target_train.append(all_target[i][j])


    for i in range(train_size, train_size + valid_size):
        for j in range(0, len(all_target[i])):
            target_valid.append(all_target[i][j])

    for i in range(train_size+valid_size, len(all_target)):
        for j in range(0, len(all_target[i])):
            target_test.append(all_target[i][j])

    print(len(input_train))
    np.savez(save_path+"_train.npz", input=input_train, target=target_train)
    np.savez(save_path+"_valid.npz", input=input_valid, target=target_valid)
    np.savez(save_path+"_test.npz", input=input_test, target=target_test)
    
# make three kinds of dataset
make_dataset(seq2seq_preprocess, paired_file_paths, 'e',
                './data/extro_seq2seq_dataset')

[list([3973, 0, 1, 2, 3, 2, 4, 5, 6, 7, 8, 3972])
 list([3973, 9, 2, 3974, 2, 11, 12, 2, 11, 12, 13, 11, 14, 15, 16, 17, 3972])
 list([3973, 3970, 19, 3970, 22, 23, 24, 25, 3970, 20, 27, 2, 11, 12, 28, 15, 29, 7, 30, 16, 23, 31, 32, 23, 33, 3972])
 list([3973, 3970, 34, 35, 36, 3970, 38, 3970, 11, 40, 41, 42, 11, 43, 44, 3970, 3970, 46, 2, 47, 32, 11, 42, 48, 49, 32, 50, 51, 23, 52, 3970, 53, 54, 32, 55, 56, 32, 57, 32, 11, 58, 23, 31, 2, 19, 58, 23, 59, 31, 60, 32, 50, 51, 61, 62, 21, 35, 11, 5, 27, 3972])
 list([3973, 27, 63, 64, 2, 2, 11, 12, 14, 15, 16, 50, 65, 66, 3972])
 list([3973, 9, 64, 64, 3970, 65, 25, 12, 3970, 65, 25, 12, 3972])
 list([3973, 9, 3970, 5, 3970, 5, 3972])
 list([3973, 67, 23, 68, 3974, 9, 3970, 3970, 72, 73, 2, 74, 75, 23, 5, 76, 77, 78, 5, 79, 3972])
 list([3973, 3974, 81, 2, 82, 83, 3972])
 list([3973, 9, 5, 84, 3970, 85, 3974, 3970, 85, 81, 2, 81, 2, 86, 87, 88, 71, 2, 89, 51, 23, 90, 91, 51, 92, 3972])
 list([3973, 93, 63, 3970, 85, 58, 27, 3970, 85, 94, 

[array([[ 0.992979  , -0.0322815 ,  0.0246271 ,  0.111101  ],
       [ 0.992685  , -0.0322274 ,  0.0267859 ,  0.113224  ],
       [ 0.992564  , -0.0320446 ,  0.0282164 ,  0.113991  ],
       ...,
       [ 0.996237  ,  0.0655421 ,  0.00639988, -0.0563455 ],
       [ 0.996245  ,  0.0649604 ,  0.0067312 , -0.0568417 ],
       [ 0.996245  ,  0.0643916 ,  0.00703811, -0.0574505 ]]), array([[ 0.997679  , -0.00396967,  0.0255913 ,  0.0629802 ],
       [ 0.997576  , -0.00474889,  0.0250169 ,  0.0647527 ],
       [ 0.997483  , -0.00549194,  0.0244312 ,  0.066343  ],
       ...,
       [ 0.99004   , -0.129474  , -0.0502541 ,  0.0230771 ],
       [ 0.989889  , -0.130362  , -0.0502551 ,  0.024494  ],
       [ 0.989758  , -0.131091  , -0.0503125 ,  0.0257292 ]]), array([[ 0.986983  , -0.116026  , -0.0039279 ,  0.111298  ],
       [ 0.986962  , -0.115807  , -0.0030584 ,  0.111737  ],
       [ 0.986968  , -0.115366  , -0.00227497,  0.112161  ],
       [ 0.987025  , -0.114699  , -0.00173339,  0.112347

[array([[ 0.999151  ,  0.00443318, -0.0216118 ,  0.0347805 ],
       [ 0.999112  ,  0.00297189, -0.0222101 ,  0.0356767 ],
       [ 0.999443  ,  0.0136    , -0.0211011 ,  0.022004  ],
       ...,
       [ 0.998636  ,  0.0420457 ,  0.0287345 , -0.0115073 ],
       [ 0.998596  ,  0.0431509 ,  0.0281922 , -0.0121978 ],
       [ 0.998628  ,  0.0427413 ,  0.0278678 , -0.0118176 ]]), array([[ 9.98900e-01,  4.27109e-02,  1.37491e-02, -1.36004e-02],
       [ 9.98861e-01,  4.36102e-02,  1.28115e-02, -1.44876e-02],
       [ 9.98883e-01,  4.33092e-02,  1.24425e-02, -1.42311e-02],
       [ 9.98875e-01,  4.39625e-02,  1.31794e-02, -1.19030e-02],
       [ 9.98908e-01,  4.33007e-02,  1.24970e-02, -1.23484e-02],
       [ 9.98956e-01,  4.24011e-02,  1.12405e-02, -1.27318e-02],
       [ 9.99101e-01,  3.95392e-02,  1.12268e-02, -1.03626e-02],
       [ 9.99249e-01,  3.63123e-02,  1.09290e-02, -7.90608e-03],
       [ 9.99265e-01,  3.59116e-02,  1.00385e-02, -8.92902e-03],
       [ 9.99405e-01,  3.27266e-02

[list([3973, 196, 1, 71, 2, 3972])
 list([3973, 9, 63, 63, 3970, 523, 36, 20, 168, 76, 3970, 462, 20, 20, 188, 133, 270, 2, 3970, 39, 134, 27, 63, 168, 3972])
 list([3973, 63, 3970, 188, 76, 3972])
 list([3973, 495, 495, 164, 7, 1062, 474, 20, 188, 168, 3972])
 list([3973, 168, 3972])
 list([3973, 27, 3970, 85, 2, 2, 19, 3970, 34, 1063, 76, 168, 63, 3974, 168, 3972])
 list([3973, 27, 211, 21, 21, 11, 3970, 26, 72, 23, 1064, 1065, 3972])
 list([3973, 3974, 270, 3972])
 list([3973, 63, 63, 63, 3970, 151, 3970, 26, 65, 1066, 134, 3970, 58, 3972])
 list([3973, 2, 19, 2, 19, 302, 2, 194, 2, 194, 23, 1062, 35, 3970, 26, 3972])
 list([3973, 270, 3970, 3970, 58, 99, 115, 20, 58, 35, 134, 3972])
 list([3973, 3970, 85, 3970, 58, 95, 3970, 248, 2, 95, 3970, 248, 2, 3972])
 list([3973, 117, 3970, 930, 270, 3974, 117, 199, 2, 191, 115, 3972])
 list([3973, 27, 3972])
 list([3973, 3974, 270, 3970, 182, 72, 1067, 134, 168, 95, 95, 3970, 3970, 151, 3970, 11, 2, 19, 1064, 1063, 32, 3970, 194, 23, 139, 1

[list([3973, 1237, 3972])
 list([3973, 9, 133, 99, 283, 2, 9, 495, 164, 625, 202, 3970, 435, 20, 98, 11, 259, 652, 35, 1238, 124, 77, 3970, 435, 9, 11, 499, 202, 3974, 9, 470, 3972])
 list([3973, 9, 3974, 9, 208, 3970, 77, 1240, 32, 3970, 77, 1241, 51, 120, 32, 187, 2, 499, 9, 470, 3972])
 list([3973, 64, 257, 2, 11, 1034, 20, 1242, 3970, 11, 9, 64, 3970, 77, 23, 133, 811, 9, 3970, 77, 272, 1243, 3970, 452, 3970, 191, 34, 20, 3972])
 list([3973, 93, 81, 2, 19, 117, 3970, 224, 58, 99, 81, 23, 421, 1244, 302, 3970, 75, 3974, 66, 499, 202, 3970, 11, 3970, 248, 370, 117, 3970, 128, 370, 32, 11, 113, 370, 283, 95, 131, 436, 878, 3970, 11, 27, 27, 2, 49, 164, 35, 151, 174, 64, 3972])
 list([3973, 27, 156, 3972])
 list([3973, 27, 174, 64, 3970, 1113, 61, 76, 1245, 174, 156, 61, 21, 65, 1014, 155, 174, 156, 76, 64, 3970, 75, 23, 47, 103, 35, 283, 117, 2, 179, 75, 23, 1246, 75, 23, 1246, 1030, 51, 35, 3972])
 list([3973, 27, 27, 27, 133, 35, 2, 58, 20, 1247, 3972])
 list([3973, 9, 63, 63, 75, 7

...

[list([3973, 156, 64, 76, 222, 2, 117, 81, 2, 179, 117, 81, 2, 179, 36, 117, 3970, 250, 99, 2, 3381, 3970, 85, 3970, 49, 164, 20, 3972])
 list([3973, 222, 2, 47, 164, 20, 3972]) list([3973, 76, 3972])
 list([3973, 76, 3972])
 list([3973, 27, 3970, 19, 3970, 23, 3382, 134, 2, 19, 3970, 103, 727, 23, 816, 51, 23, 3383, 50, 39, 11, 3384, 3972])
 list([3973, 3970, 85, 3970, 3970, 77, 382, 29, 297, 507, 860, 71, 3970, 3972])
 list([3973, 3970, 3972])
 list([3973, 134, 2, 19, 76, 2, 19, 3974, 76, 2, 19, 2, 920, 7, 757, 330, 93, 3974, 11, 58, 3970, 503, 32, 3385, 3974, 3972])
 list([3973, 27, 134, 2, 19, 3970, 76, 2, 3970, 75, 99, 81, 249, 2, 11, 75, 99, 100, 39, 3974, 3970, 100, 3156, 882, 2, 184, 75, 23, 1875, 153, 3970, 253, 99, 523, 36, 3972])
 list([3973, 3970, 75, 23, 1875, 2, 3970, 509, 75, 99, 115, 277, 3974, 3970, 85, 11, 179, 36, 20, 3974, 330, 23, 816, 3383, 32, 179, 36, 35, 3387, 35, 1423, 800, 499, 153, 3972])
 list([3973, 134, 3970, 3972])
 list([3973, 93, 2, 19, 61, 21, 280, 20

[array([[ 0.999661  ,  0.00369607, -0.00674049,  0.0248819 ],
       [ 0.999602  ,  0.00373388, -0.00637344,  0.0272352 ],
       [ 0.999528  ,  0.00396116, -0.00584869,  0.0299009 ],
       ...,
       [ 0.999822  ,  0.00479925,  0.00516317, -0.017525  ],
       [ 0.999801  ,  0.00541783,  0.00369196, -0.0188626 ],
       [ 0.999769  ,  0.00601327,  0.0022696 , -0.0205271 ]]), array([[ 9.99708e-01,  1.23837e-02,  1.27942e-03, -2.07136e-02],
       [ 9.99711e-01,  1.22646e-02,  1.11288e-03, -2.06369e-02],
       [ 9.99715e-01,  1.21656e-02,  9.00254e-04, -2.05346e-02],
       ...,
       [ 9.97526e-01, -1.25235e-02,  1.90384e-02, -6.65040e-02],
       [ 9.97580e-01, -1.23948e-02,  1.88298e-02, -6.57739e-02],
       [ 9.97617e-01, -1.23294e-02,  1.85417e-02, -6.53094e-02]]), array([[ 9.97973e-01, -1.94150e-03,  4.66257e-02,  4.32625e-02],
       [ 9.98133e-01, -2.01549e-03,  4.49272e-02,  4.13341e-02],
       [ 9.98273e-01, -1.90673e-03,  4.30752e-02,  3.98975e-02],
       [ 9.98380e-01

[list([3973, 9, 766, 4, 103, 61, 297, 3970, 205, 4, 103, 7, 129, 3732, 3972])
 list([3973, 9, 4, 103, 7, 2243, 153, 7, 1342, 32, 50, 7, 50, 7, 3733, 61, 21, 208, 3970, 34, 20, 126, 3972])
 list([3973, 9, 93, 3974, 81, 46, 81, 2, 464, 578, 3972])
 list([3973, 117, 36, 9, 9, 4, 103, 409, 409, 3735, 153, 35, 3296, 3970, 578, 39, 3970, 3736, 9, 3970, 11, 208, 3970, 34, 20, 3972])
 list([3973, 9, 133, 75, 23, 1450, 3972])
 list([3973, 32, 3970, 7, 476, 2298, 365, 883, 32, 4, 103, 7, 2539, 9, 365, 883, 3970, 145, 180, 23, 180, 23, 23, 166, 64, 746, 288, 61, 21, 208, 3970, 145, 72, 12, 29, 23, 3737, 90, 288, 3970, 64, 1841, 3970, 3738, 3972])
 list([3973, 9, 134, 3970, 34, 121, 3970, 3970, 72, 81, 3970, 2, 58, 121, 3972])
 list([3973, 117, 211, 3972])
 list([3973, 9, 3970, 452, 3970, 11, 29, 65, 3739, 3970, 452, 3970, 452, 3970, 3970, 72, 58, 20, 3970, 85, 3970, 219, 2526, 61, 21, 23, 844, 211, 3970, 326, 239, 99, 23, 121, 90, 75, 124, 157, 12, 99, 146, 288, 61, 3974, 3972])
 list([3973, 9, 3

[list([3973, 196, 3970, 1105, 3972])
 list([3973, 3974, 3974, 117, 81, 2, 85, 117, 81, 3970, 179, 3972])
 list([3973, 3974, 63, 20, 3970, 515, 75, 2, 75, 2, 3268, 2201, 3972])
 list([3973, 388, 3972]) list([3973, 93, 3970, 85, 3972])
 list([3973, 3970, 26, 133, 3972]) list([3973, 168, 3972])
 list([3973, 3970, 85, 3970, 835, 3972])
 list([3973, 156, 58, 3974, 388, 3972])
 list([3973, 394, 98, 1355, 2018, 2291, 330, 23, 1019, 164, 23, 840, 1657, 3970, 85, 61, 21, 61, 21, 3783, 3972])
 list([3973, 122, 1019, 3970, 394, 250, 35, 3972])
 list([3973, 63, 3970, 26, 117, 124, 180, 288, 188, 188, 188, 1813, 280, 3974, 280, 81, 2, 920, 99, 1590, 20, 3972])
 list([3973, 600, 1347, 3970, 334, 164, 3970, 334, 164, 2018, 2291, 3970, 58, 840, 2201, 23, 3784, 61, 21, 3783, 3972])
 list([3973, 501, 71, 2, 1151, 61, 21, 3974, 61, 21, 3783, 3972])
 list([3973, 3970, 3785, 61, 1657, 21, 1328, 1, 249, 222, 2, 372, 153, 1354, 61, 21, 61, 21, 3974, 58, 61, 21, 3783, 3972])
 list([3973, 63, 3970, 2905, 35, 3

[list([3973, 196, 952, 196, 470, 3970, 20, 239, 3972])
 list([3973, 27, 452, 196, 3974, 470, 81, 2, 464, 47, 164, 23, 47, 164, 23, 529, 88, 212, 470, 3972])
 list([3973, 151, 151, 3972])
 list([3973, 27, 452, 3974, 3974, 3974, 288, 2, 81, 11, 3974, 436, 3970, 1812, 702, 699, 3970, 77, 58, 3970, 480, 1481, 279, 319, 32, 3970, 11, 435, 2, 19, 124, 262, 3974, 3972])
 list([3973, 3970, 3974, 1481, 3972]) list([3973, 27, 452, 470, 3972])
 list([3973, 9, 1247, 27, 289, 146, 63, 3970, 11, 3901, 134, 27, 47, 153, 3974, 3972])
 list([3973, 27, 27, 3972]) list([3973, 9, 1247, 3972])
 list([3973, 27, 27, 3972])
 list([3973, 3974, 3974, 117, 2, 496, 470, 3972])
 list([3973, 27, 27, 3972])
 list([3973, 940, 699, 3974, 279, 3903, 940, 699, 214, 2, 1640, 3972])
 list([3973, 3970, 781, 3974, 515, 2, 496, 279, 3903, 940, 699, 230, 3970, 3974, 3970, 47, 99, 23, 2207, 174, 458, 3970, 465, 99, 7, 92, 93, 3974, 93, 3970, 11, 465, 16, 7, 92, 283, 3972])
 list([3973, 93, 3970, 2487, 2, 319, 35, 940, 699, 35,

In [10]:
#%%
# this code is to make dataset for seq2seq baseline model
the_path = '/afs/inf.ed.ac.uk/group/cstr/projects/galatea/d02'
data_path_motion = the_path + '/Recordings_October_2014/DOF-hiroshi/'
data_path_text = the_path + '/Recordings_October_2014/Transcriptions/transcriptions_phrase_tables/'

paired_file_paths = pair_files(data_path_text, '.TABLE', data_path_motion,
                                '.qtn')




# make three kinds of dataset
make_dataset(seq2seq_preprocess, paired_file_paths, 'e',
                './data/extro_seq2seq_dataset')
print('extroverted data finished')
make_dataset(seq2seq_preprocess, paired_file_paths, 'i',
                './data/intro_seq2seq_dataset')
print('introverted data finished')
make_dataset(seq2seq_preprocess, paired_file_paths, 'n',
                './data/natural_seq2seq_dataset')
print('natural data finished')

22
22
50
50
46
46
47
47
34
34
56
56
50
50
49
49
48
48
33
33


KeyboardInterrupt: 

## Building the models

In [ ]:
MAX_LENGTH = 100


USE_CUDA = True



In [ ]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size, n_layers=1):
        super(EncoderRNN, self).__init__()
        
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.n_layers = n_layers
        
        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size, n_layers)
        
    def forward(self, word_inputs, hidden):
        # Note: we run this all at once (over the whole input sequence)
        seq_len = len(word_inputs)
        embedded = self.embedding(word_inputs).view(seq_len, 1, -1)
        output, hidden = self.gru(embedded, hidden)
        return output, hidden

    def init_hidden(self):
        hidden = Variable(torch.zeros(self.n_layers, 1, self.hidden_size))
        if USE_CUDA: hidden = hidden.cuda()
        return hidden

In [ ]:
class BahdanauAttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, n_layers=1, dropout_p=0.1):
        super(AttnDecoderRNN, self).__init__()
        
        # Define parameters
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.n_layers = n_layers
        self.dropout_p = dropout_p
        self.max_length = max_length
        
        # Define layers
        self.embedding = nn.Embedding(output_size, hidden_size)
        self.dropout = nn.Dropout(dropout_p)
        self.attn = GeneralAttn(hidden_size)
        self.gru = nn.GRU(hidden_size * 2, hidden_size, n_layers, dropout=dropout_p)
        self.out = nn.Linear(hidden_size, output_size)
    
    def forward(self, word_input, last_hidden, encoder_outputs):
        # Note that we will only be running forward for a single decoder time step, but will use all encoder outputs
        
        # Get the embedding of the current input word (last output word)
        word_embedded = self.embedding(word_input).view(1, 1, -1) # S=1 x B x N
        word_embedded = self.dropout(word_embedded)
        
        # Calculate attention weights and apply to encoder outputs
        attn_weights = self.attn(last_hidden[-1], encoder_outputs)
        context = attn_weights.bmm(encoder_outputs.transpose(0, 1)) # B x 1 x N
        
        # Combine embedded input word and attended context, run through RNN
        rnn_input = torch.cat((word_embedded, context), 2)
        output, hidden = self.gru(rnn_input, last_hidden)
        
        # Final output layer
        output = output.squeeze(0) # B x N
        output = F.log_softmax(self.out(torch.cat((output, context), 1)))
        
        # Return final output, hidden state, and attention weights (for visualization)
        return output, hidden, attn_weights

In [ ]:
class Attn(nn.Module):
    def __init__(self, method, hidden_size, max_length=MAX_LENGTH):
        super(Attn, self).__init__()
        
        self.method = method
        self.hidden_size = hidden_size
        
        if self.method == 'general':
            self.attn = nn.Linear(self.hidden_size, hidden_size)

        elif self.method == 'concat':
            self.attn = nn.Linear(self.hidden_size * 2, hidden_size)
            self.other = nn.Parameter(torch.FloatTensor(1, hidden_size))

    def forward(self, hidden, encoder_outputs):
        seq_len = len(encoder_outputs)

        # Create variable to store attention energies
        attn_energies = Variable(torch.zeros(seq_len)) # B x 1 x S
        if USE_CUDA: attn_energies = attn_energies.cuda()

        # Calculate energies for each encoder output
        for i in range(seq_len):
            attn_energies[i] = self.score(hidden, encoder_outputs[i])

        # Normalize energies to weights in range 0 to 1, resize to 1 x 1 x seq_len
        return F.softmax(attn_energies).unsqueeze(0).unsqueeze(0)
    
    def score(self, hidden, encoder_output):
        
        if self.method == 'dot':
            energy = hidden.dot(encoder_output)
            return energy
        
        elif self.method == 'general':
            energy = self.attn(encoder_output)
            energy = hidden.dot(energy)
            return energy
        
        elif self.method == 'concat':
            energy = self.attn(torch.cat((hidden, encoder_output), 1))
            energy = self.other.dot(energy)
            return energy

In [ ]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, attn_model, hidden_size, output_size, n_layers=1, dropout_p=0.1):
        super(AttnDecoderRNN, self).__init__()
        
        # Keep parameters for reference
        self.attn_model = attn_model
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.n_layers = n_layers
        self.dropout_p = dropout_p
        
        # Define layers
        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size * 2, hidden_size, n_layers, dropout=dropout_p)
        self.out = nn.Linear(hidden_size * 2, output_size)
        
        # Choose attention model
        if attn_model != 'none':
            self.attn = Attn(attn_model, hidden_size)
    
    def forward(self, word_input, last_context, last_hidden, encoder_outputs):
        # Note: we run this one step at a time
        
        # Get the embedding of the current input word (last output word)
        word_embedded = self.embedding(word_input).view(1, 1, -1) # S=1 x B x N
        
        # Combine embedded input word and last context, run through RNN
        rnn_input = torch.cat((word_embedded, last_context.unsqueeze(0)), 2)
        rnn_output, hidden = self.gru(rnn_input, last_hidden)

        # Calculate attention from current RNN state and all encoder outputs; apply to encoder outputs
        attn_weights = self.attn(rnn_output.squeeze(0), encoder_outputs)
        context = attn_weights.bmm(encoder_outputs.transpose(0, 1)) # B x 1 x N
        
        # Final output layer (next word prediction) using the RNN hidden state and context vector
        rnn_output = rnn_output.squeeze(0) # S=1 x B x N -> B x N
        context = context.squeeze(1)       # B x S=1 x N -> B x N
        output = F.log_softmax(self.out(torch.cat((rnn_output, context), 1)))
        
        # Return final output, hidden state, and attention weights (for visualization)
        return output, context, hidden, attn_weights

In [ ]:
# encoder_test = EncoderRNN(10, 10, 2)
# decoder_test = AttnDecoderRNN('general', 10, 10, 2)
# print(encoder_test)
# print(decoder_test)

# encoder_hidden = encoder_test.init_hidden()
# word_input = Variable(torch.LongTensor([1, 2, 3]))
# if USE_CUDA:
#     encoder_test.cuda()
#     word_input = word_input.cuda()
# encoder_outputs, encoder_hidden = encoder_test(word_input, encoder_hidden)

# word_inputs = Variable(torch.LongTensor([1, 2, 3]))
# decoder_attns = torch.zeros(1, 3, 3)
# decoder_hidden = encoder_hidden
# decoder_context = Variable(torch.zeros(1, decoder_test.hidden_size))

# if USE_CUDA:
#     decoder_test.cuda()
#     word_inputs = word_inputs.cuda()
#     decoder_context = decoder_context.cuda()

# for i in range(3):
#     decoder_output, decoder_context, decoder_hidden, decoder_attn = decoder_test(word_inputs[i], decoder_context, decoder_hidden, encoder_outputs)
#     print(decoder_output.size(), decoder_hidden.size(), decoder_attn.size())
#     decoder_attns[0, i] = decoder_attn.squeeze(0).cpu().data


## Train

In [ ]:
batch_size = 50

extro_data_train_path = './data/extro_seq2seq_dataset_train.npz'
extro_data_valid_path = './data/extro_seq2seq_dataset_valid.npz'
extro_data_test_path = './data/extro_seq2seq_dataset_test.npz'

intro_data_train_path = './data/intro_seq2seq_dataset_train.npz'
intro_data_valid_path = './data/intro_seq2seq_dataset_valid.npz'
intro_data_test_path = './data/intro_seq2seq_dataset_test.npz'

natural_data_train_path = './data/natural_seq2seq_dataset_train.npz'
natural_data_valid_path = './data/natural_seq2seq_dataset_valid.npz'
natural_data_test_path = './data/natural_seq2seq_dataset_test.npz'
# data_path = './data/extro_seq2seq_dataset.npz'
word2idx = vocab_to_int  # load word map
#
# # load and split dataset
# seq2seq_dataset = Seq2SeqDataset(data_path, word2idx)
# train_size = int(0.8 * len(seq2seq_dataset))
# valid_size = int(0.1 * len(seq2seq_dataset))
# test_size = len(seq2seq_dataset) - train_size - valid_size

# train_set, valid_set, test_set = random_split(
    # seq2seq_dataset, [train_size, valid_size, test_size])

train_set = Seq2SeqDataset(extro_data_train_path, word2idx)
valid_set = Seq2SeqDataset(extro_data_valid_path, word2idx)
test_set = Seq2SeqDataset(extro_data_test_path, word2idx)
# print(len(valid_set))
# print(test_set[0])

input_test_set = []
target_test_set = []
for i in range(0, len(test_set)):
    input_test_set.append(test_set[i][0])
    target_test_set.append(test_set[i][1])

np.savez("test_data.npz", input=input_test_set, target=target_test_set)


train_dataloader = DataLoader(train_set,
                              batch_size,
                              shuffle=True,
                              collate_fn=seq2seq_collate_fn)
valid_dataloader = DataLoader(valid_set,
                              batch_size,
                              shuffle=True,
                              collate_fn=seq2seq_collate_fn)
test_dataloader = DataLoader(test_set,
                             batch_size=1,
                             collate_fn=seq2seq_collate_fn)



In [ ]:
teacher_forcing_ratio = 0.5
clip = 5.0

def train(input_variable, target_variable, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):

    # Zero gradients of both optimizers
    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()
    loss = 0 # Added onto for each word

    # Get size of input and target sentences
    input_length = input_variable.size()[0]
    target_length = target_variable.size()[0]

    # Run words through encoder
    encoder_hidden = encoder.init_hidden()
    encoder_outputs, encoder_hidden = encoder(input_variable, encoder_hidden)
    
    # Prepare input and output variables
    decoder_input = Variable(torch.LongTensor([[SOS_token]]))
    decoder_context = Variable(torch.zeros(1, decoder.hidden_size))
    decoder_hidden = encoder_hidden # Use last hidden state from encoder to start decoder
    if USE_CUDA:
        decoder_input = decoder_input.cuda()
        decoder_context = decoder_context.cuda()

    # Choose whether to use teacher forcing
    use_teacher_forcing = random.random() < teacher_forcing_ratio
    if use_teacher_forcing:
        
        # Teacher forcing: Use the ground-truth target as the next input
        for di in range(target_length):
            decoder_output, decoder_context, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_context, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_variable[di])
            decoder_input = target_variable[di] # Next target is next input

    else:
        # Without teacher forcing: use network's own prediction as the next input
        for di in range(target_length):
            decoder_output, decoder_context, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_context, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_variable[di])
            
            # Get most likely word index (highest value) from output
            topv, topi = decoder_output.data.topk(1)
            ni = topi[0][0]
            
            decoder_input = Variable(torch.LongTensor([[ni]])) # Chosen word is next input
            if USE_CUDA: decoder_input = decoder_input.cuda()

            # Stop at end of sentence (not necessary when using known targets)
            if ni == EOS_token: break

    # Backpropagation
    loss.backward()
    torch.nn.utils.clip_grad_norm(encoder.parameters(), clip)
    torch.nn.utils.clip_grad_norm(decoder.parameters(), clip)
    encoder_optimizer.step()
    decoder_optimizer.step()
    
    return loss.data[0] / target_length

In [ ]:
def as_minutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)

def time_since(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (as_minutes(s), as_minutes(rs))

In [ ]:
attn_model = 'general'

hidden_size = 500
n_layers = 2
dropout_p = 0.05
embed_dim = 100

# Initialize models
encoder = EncoderRNN(embed_dim, hidden_size, n_layers)
decoder = AttnDecoderRNN(attn_model, hidden_size, embed_dim, n_layers, dropout_p=dropout_p)

# Move models to GPU
if USE_CUDA:
    encoder.cuda()
    decoder.cuda()

# Initialize optimizers and criterion
learning_rate = 0.0001
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate)
criterion = nn.NLLLoss()


In [ ]:


# Configuring training
n_epochs = 50000
plot_every = 200
print_every = 1000

# Keep track of time elapsed and running averages
start = time.time()
plot_losses = []
print_loss_total = 0 # Reset every print_every
plot_loss_total = 0 # Reset every plot_every



In [ ]:
for idx, (in_seq, tgt_seq, target, in_len, tgt_len) in enumerate(train_dataloader):

#         in_seq = in_seq.to(device)
#         tgt_seq = tgt_seq.to(device)
#         target = target.to(device)
#         in_len = in_len.to(device)
#         tgt_len = tgt_len.to(device)

In [ ]:
# Begin!
for epoch in range(1, n_epochs + 1):
    
    # Get training data for this cycle
    training_pair = train_dataloader
    input_variable = training_pair[0]
    target_variable = training_pair[1]

    # Run the train function
    loss = train(input_variable, target_variable, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion)

    # Keep track of loss
    print_loss_total += loss
    plot_loss_total += loss

    if epoch == 0: continue

    if epoch % print_every == 0:
        print_loss_avg = print_loss_total / print_every
        print_loss_total = 0
        print_summary = '%s (%d %d%%) %.4f' % (time_since(start, epoch / n_epochs), epoch, epoch / n_epochs * 100, print_loss_avg)
        print(print_summary)

    if epoch % plot_every == 0:
        plot_loss_avg = plot_loss_total / plot_every
        plot_losses.append(plot_loss_avg)
        plot_loss_total = 0